In [4]:
import numpy as np
import math
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from mpl_toolkits.mplot3d import Axes3D
from mpl_toolkits.mplot3d.art3d import Poly3DCollection, Line3DCollection

#### This final project animates cube of jello falling on a trampoline. 
##### The jello is cube is represented as 8 points at the corners of the cube connected by springs and one corner at the center of the cube. All the points are of equal mass. 

In [10]:
def RungeKutta(u0,dt,T,nOut):

    # The trajectory is solved in the time interval [0,T]
    # with dt time steps.  The trajectory is saved less frequently, 
    # every T/nOut time step
    
    nInner = math.ceil(T/nOut/dt)
    Dt = nInner * dt
    
    m,n = np.shape(u0)
    trajectory = np.zeros((m,n,nOut))  
    
    for it1 in range(nOut):
        for it2 in range(nInner):
            du1 = dt * dudt(u0);
            du2 = dt * dudt(u0+0.5*du1);
            du3 = dt * dudt(u0+0.5*du2); 
            du4 = dt * dudt(u0+du3)
            u0  = u0 + (du1 + 2 * du2 + 2 * du3 + du4 ) / 6            
        trajectory[:,:,it1]=u0
    return (trajectory,Dt)

In [11]:
# Equation of motion
    
def dudt(u):
    # u is the state variable
    # u has nPoints * 6 entries
    # there are 3 position variables for each point
    # there are 3 velocity variable for each point
    # first nPoints * 3 variables are positions
    # last nPoints * 3 variables are velocities
    
    # global variables: neutralSpringLength, springStiffness, groundStiffness, damping, mass, g
    
    nPoints, n = np.shape(u)
    
    # udot is the time derivative of the state variable
    udot = np.zeros( (nPoints, n) )
    
    udot[:,0:3] = u[:,3:6] # time derivative of position is velocity
    
    tiny = 1e-6  # to avoid dividing by zero when computing a unit vector

    for p in range(nPoints):
        
        # ground pushes back an object that goes below z=0
        groundReaction = groundStiffness * max(0,-u[p,2])
        friction = -u[p,3:6] * damping
        
        udot[p,3:6] =  ( groundReaction + friction )/mass + g

        for q in range(nPoints):
            
            if springStiffness[p,q]>0:
                du = u[q,0:3]-u[p,0:3]
                springLength = np.linalg.norm( du )
                unitVector = du / ( springLength + tiny )
                strain = ( springLength - neutralSpringLength[p,q] ) / neutralSpringLength[p,q]
                springForce = springStiffness[p,q] * strain * unitVector
            else:
                springForce = 0

            udot[p,3:6] = udot[p,3:6] + springForce / mass
                  
    return(udot)
        

In [6]:
def meshgrid3d(x,y,z):

    pts = np.zeros( (len(x)*len(y)*len(z)+1, 3))
    n = 0
    for a in x:
        for b in y:
            for c in z:
                pts[n,:]=np.array([a,b,c])
                n=n+1    
    return(pts)

In [12]:
def rotate(p,alpha,beta,gamma):
    
    # rigid body rotation
    
    c = np.cos(alpha)
    s = np.sin(alpha)
    p = np.matmul(p,np.array([[c,s,0],[-s,c,0],[0,0,1]]))
    
    c = np.cos(beta)
    s = np.sin(beta)
    p = np.matmul(p,np.array([[c,0,s],[0,1,0],[-s,0,c]]))
    
    c = np.cos(gamma)
    s = np.sin(gamma)
    p = np.matmul(p,np.array([[1,0,0],[0,c,s],[0,-s,c]]))
    
    return(p)
    

In [9]:
#initial conditions
mass = 1  
k1 = 2  # spring stiffness = tension/strain
initialHeight = 1
g = np.array([0,0,-0.5])
groundStiffness = np.array([0,0,2])
damping = 0.1
dt = 0.0003  # larger dt not be stable
T = 20
nOut = 500

#Making the 1X1X1 jello cube
points = meshgrid3d( [0,1], [0,1], [0,1] ) #corner points
points[8,:] = np.array([0.5,0.5,0.5]) #center point

#Setting the neutral spring lenght to initial distance between points
neutralSpringLength = np.zeros((len(points),len(points)))
for i in range(len(points)):
    for j in range(len(points)):
        neutralSpringLength[i,j] = np.linalg.norm(points[i,:]-points[j,:])
        
#if points are connected by springs they should have spring stiffness of k1, otherwise stiffness is zero
springStiffness   = np.zeros((len(points),len(points)))
for i in range(len(points)):
    for j in range(len(points)):
        if any( points[i,:] == points[j,:] ) and i!=j :
            springStiffness[i,j]=k1

#making the sides of the cube by using 3 connecting points in the cube to make triangles. 
#each of the 6 sides of the cube are made up by 4 triangles
faces = np.zeros((6*4,3,3))
m=0
for ii in range(3):
    for x0 in [0,1]:
        mask = points[:,ii]==x0
        p0 = pt[mask,:]
        p0m = np.mean(p0,axis=0)           
        faces[m  ,:,:] = [p0[0,:],p0[1,:],p0m]
        faces[m+1,:,:] = [p0[1,:],p0[3,:],p0m]
        faces[m+2,:,:] = [p0[2,:],p0[3,:],p0m]
        faces[m+3,:,:] = [p0[0,:],p0[2,:],p0m]
        m=m+4


fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')

r = [-1,8]

X, Y = np.meshgrid(r, r)
# plot vertices
ax.scatter3D(points[:, 0], points[:, 1], points[:, 2])


# plot sides of cube
collection=(Poly3DCollection(faces,facecolors='cyan', linewidths=1, edgecolors='r', alpha=.25))
face_color = [0.5, 0.5, 1]
collection.set_facecolor(face_color)
ax.add_collection3d(collection)


ax.set_xlabel('X')
ax.set_ylabel('Y')
ax.set_zlabel('Z')

plt.show()

NameError: name 'pt' is not defined